### More accurate derivatives

( see https://en.wikipedia.org/wiki/Five-point_stencil )

Taylor series 

$
f(x+h)=f(x) + f'(x)h + \frac{f''(x)h^{2}}{2!} + \frac{f'''(x)h^3}{3!}+ \ldots
$

lets discretize $x$ with a step size $h$ i.e.

$
x_j=x_0 + h(j-1)
$

we can the write

$ f(x_{j-2}) \approx f(x_j) - f'(x_j)2h + \frac{1}{2}f''(x_j)4h^{2} - \frac{1}{6}f'''(x_j)8h^3 + \frac{1}{24}f''''(x_j)16h^4 - \frac{1}{120}f'''''(x_j)32h^5 + \ldots $

$ f(x_{j-1}) \approx f(x_j) - f'(x_j)h  + \frac{1}{2}f''(x_j)h^{2} - \frac{1}{6}f'''(x_j)h^3 + \frac{1}{24}f''''(x_j)h^4 - \frac{1}{120}f'''''(x_j)h^5 + \ldots $

$ f(x_{j-1}) \approx f(x_j) + f'(x_j)h  + \frac{1}{2}f''(x_j)h^{2} + \frac{1}{6}f'''(x_j)h^3 + \frac{1}{24}f''''(x_j)h^4 + \frac{1}{120}f'''''(x_j)h^5 + \ldots $

$ f(x_{j+2}) \approx f(x_j) + f'(x_j)2h + \frac{1}{2}f''(x_j)4h^{2} + \frac{1}{6}f'''(x_j)8h^3 + \frac{1}{24}f''''(x_j)16h^4 + \frac{1}{120}f'''''(x_j)32h^5 + \ldots $

and then rearrange for $f'(x_j)$

$
f'(x_j) \approx \frac{f(x_{j-2})-8f(x_{j-1})+8f(x_{j+1})+f(x_{j+2})}{12h}
 + \ldots 
$




In [17]:
#
# Lets test these formulas
#
import numpy as np
import matplotlib.pyplot as plt
h=0.005;
L=2*np.pi;N=np.round(L/h)+1;h=L/(N-1)
x=np.linspace(0,L,int(N) )

def ff(x,L):
    return np.cos(x/L*np.pi*2)

def fop(xvec, L, f):
    ans=np.zeros(np.size(xvec))
    i=0
    for x in xvec:
        ans[i]=f(x, L)
        i+=1
    return ans

fx=fop(x, L, ff)

In [18]:
def deriv1(fx,h):
    deriv=fx[1:]-fx[0:-1]
    deriv=deriv/h
    return deriv

def deriv2(fx,h):
    deriv=fx[2:]-fx[0:-2]
    deriv=deriv/(2*h)
    return deriv

def deriv5(fx,h):
    fxm2=fx[0:-4]
    fxm1=fx[1:-3]
    fx_0=fx[2:-2]
    fxp1=fx[3:-1]
    fxp2=fx[4:]
    deriv=fxm2-8*fxm1+8*fxp1-fxp2
    deriv=deriv/(12*h)
    return deriv

In [19]:
d1=deriv1(fx,h)
d2=deriv2(fx,h)
d5=deriv5(fx,h)

In [ ]:
plt.plot(x,fx)
plt.plot(x[1:],d1)
plt.plot(x[1:],-np.sin(x[1:]/L*np.pi*2))
plt.show()
plt.plot(x[1:],d1+np.sin(x[1:]/L*np.pi*2))
plt.show()
e1=np.linalg.norm( d1+np.sin(x[1:]/L*np.pi*2) )
print(e1)

In [ ]:
plt.plot(x[1:-1],d2)
plt.show()
plt.plot(x[1:-1],d2+np.sin(x[1:-1]/L*np.pi*2))
plt.show()
e2=np.linalg.norm( d2+np.sin(x[1:-1]/L*np.pi*2) )
print(e2)

In [ ]:
plt.plot(x[2:-2],d5)
plt.show()
plt.plot(x[2:-2],d5+np.sin(x[2:-2]/L*np.pi*2))
plt.show()
e5=np.linalg.norm( d5+np.sin(x[2:-2]/L*np.pi*2) )
print("Error in deriv5",e5)

In [23]:
# Now lets look at convergence
def get_x(h):
    L=2*np.pi;N=np.round(L/h)+1;h=L/(N-1)
    x=np.linspace(0,L,int(N) )
    return x, h

h=0.05
nh=5
e1vec=np.zeros(nh)
e2vec=np.zeros(nh)
e5vec=np.zeros(nh)
hvec=np.zeros(nh)

for i in [*range(0,nh)]:
    x,h=get_x(h)
    fx=fop(x, L, ff)
    d1=deriv1(fx,h)
    e1vec[i]=np.linalg.norm( d1+np.sin(x[1:]/L*np.pi*2) )
    d2=deriv2(fx,h)
    e2vec[i]=np.linalg.norm( d2+np.sin(x[1:-1]/L*np.pi*2) )
    d5=deriv5(fx,h)
    e5vec[i]=np.linalg.norm( d5+np.sin(x[2:-2]/L*np.pi*2) )
    hvec[i]=h
    h=h/2

In [ ]:
%matplotlib inline
#%matplotlib ipympl
plt.figure
plt.plot(x[1:], d1+np.sin(x[1:]/L*np.pi*2) )
plt.show()
plt.figure
plt.plot(x[1:-1],d2+np.sin(x[1:-1]/L*np.pi*2) )
plt.show()
plt.figure

plt.plot(x[2:-2],d5 + np.sin(x[2:-2]/L*np.pi*2) )
plt.show()

In [ ]:
# Use the ipympl backend so that we can Zoom figure (need to re-run this
# cell to make interactive again)
%matplotlib ipympl
plt.plot(x[2:-2],d5 + np.sin(x[2:-2]/L*np.pi*2) )
plt.show()

In [ ]:
%matplotlib inline

plt.semilogy(e1vec/e1vec[0],'.')
plt.show()
plt.semilogy(e2vec/e2vec[0],'.')
plt.show()
plt.semilogy(e5vec/e5vec[0],'.')
plt.show()

In [ ]:
hvec